## Optimize marketing expenses for Yandex.Afisha

I work in the analytical department at Yandex.Afisha, and my job is to help optimize marketing expenses.<br>
Yandex.Afisha is a service for selling tickets to entertainment events.<br>
Using the product, sales, and marketing data of our application - and with the help of user behavior analysis and various KPIs, we will try to find the most important sources that we would recommend the company to invest in.

<a class="anchor" id="T.O.C"></a>

<h2> Table of Contents </h2>

* [Step 1.Download the data and prepare it for analysis.](#step1)
    * [Step 1.1 Preparation and optimization of vists file](#step1.1)
    * [Step 1.2 Preparation and optimization of order file](#step1.2)
    * [Step 1.3 Preparation and optimization of costs file](#step1.3)
<br><br>
* [Step 2. Make reports and calculate metrics.](#step2)
    * [step 2.1 Product](#step2.1)
    * [Step 2.2 Sales](#step2.2)
    * [Step 2.3 Marketing](#step2.3)
<br><br>
* [Step 3. Conclusion](#step3)
  
    

 [Go Up.](#T.O.C)⏫

# Step 1. Download the data and prepare it for analysis <a class="anchor" id="step1"></a>

In [177]:
import pandas as pd
import numpy  as np

import math
from scipy import stats as st

import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.offline import iplot



df_visits = pd.read_csv("/datasets/visits_log_us.csv")
df_orders = pd.read_csv("/datasets/orders_log_us.csv")
df_costs  = pd.read_csv("/datasets/costs_us.csv")

We will now open the data, prepare it for analysis and optimization

## step 1.1 Preparation and optimization of /datasets/visits_log_us.csv (df_visits):<a class="anchor" id="step1.1"></a>


 [Go Up.](#T.O.C)⏫

**We will start researching the first file-**

In [178]:
df_visits.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 359400 entries, 0 to 359399
Data columns (total 5 columns):
Device       359400 non-null object
End Ts       359400 non-null object
Source Id    359400 non-null int64
Start Ts     359400 non-null object
Uid          359400 non-null uint64
dtypes: int64(1), object(3), uint64(1)
memory usage: 13.7+ MB


### First overlook:
1. There seems to be no "null" values, excellent!
2. There are two columns that are not in the desired type: "End Ts" and "Start Ts", we need to change them.
3. The column names start with capital letters, we will change them to small letters.
4. The memory usage is 13.7+ MB, we will try to study more about it and optimize it.

In [179]:
df_visits.sample(5)

Device               End Ts  Source Id             Start Ts  \
44312   desktop  2018-01-28 23:04:00          4  2018-01-28 22:29:00   
185914  desktop  2018-03-29 13:06:00          3  2018-03-29 13:06:00   
143107  desktop  2017-12-03 02:29:00          9  2017-12-03 02:26:00   
170469  desktop  2018-02-09 03:10:00          4  2018-02-09 02:41:00   
257406  desktop  2017-11-27 16:07:00          1  2017-11-27 15:19:00   

                         Uid  
44312    4105809592569498827  
185914  18242620185606016147  
143107   3532988459584569512  
170469  13319142244260672945  
257406   8515175948176738299

### Data optimization:

Lets foud out how big the file is:

In [180]:
df_visits.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 359400 entries, 0 to 359399
Data columns (total 5 columns):
Device       359400 non-null object
End Ts       359400 non-null object
Source Id    359400 non-null int64
Start Ts     359400 non-null object
Uid          359400 non-null uint64
dtypes: int64(1), object(3), uint64(1)
memory usage: 79.3 MB


The memory usage Before is: 79.3 MB

**We will change the column names, data types, and then check the memory usage after-**

In [181]:
# Change from capital to small letters:
df_visits.columns = df_visits.columns.str.lower()
df_visits = df_visits.rename(columns = {"end ts":"end_ts","start ts":"start_ts","source id":"source_id"})
df_visits.columns

Index(['device', 'end_ts', 'source_id', 'start_ts', 'uid'], dtype='object')

In [182]:
#Change to Date and Time type:
df_visits['start_ts'] =  pd.to_datetime(df_visits['start_ts'], format='%Y-%m-%d %H:%M:%S')
df_visits['end_ts'] =  pd.to_datetime(df_visits['end_ts'], format='%Y-%m-%d %H:%M:%S')

In [183]:
#Change to Category:
print(df_visits['device'].value_counts())
df_visits['device'] = df_visits['device'].astype('category')
print(df_visits['device'].value_counts())


desktop    262567
touch       96833
Name: device, dtype: int64
desktop    262567
touch       96833
Name: device, dtype: int64


**Now we'll check the memory usage after optimization:**

In [184]:
df_visits.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 359400 entries, 0 to 359399
Data columns (total 5 columns):
device       359400 non-null category
end_ts       359400 non-null datetime64[ns]
source_id    359400 non-null int64
start_ts     359400 non-null datetime64[ns]
uid          359400 non-null uint64
dtypes: category(1), datetime64[ns](2), int64(1), uint64(1)
memory usage: 11.3 MB


### Great, we reduced the memory usage by almost 90%!

## step 1.2 Preparation and optimization of /datasets/orders_log_us.csv (df_orders):<a class="anchor" id="step1.2"></a>


 [Go Up.](#T.O.C)⏫

**We will researching the third file-**

In [185]:
df_orders.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50415 entries, 0 to 50414
Data columns (total 3 columns):
Buy Ts     50415 non-null object
Revenue    50415 non-null float64
Uid        50415 non-null uint64
dtypes: float64(1), object(1), uint64(1)
memory usage: 1.2+ MB


### First overlook:
1. There seems to be no "null" values, excellent!
2. There are one column that are not in the desired type: Buy Ts, we need to change it to date and time type.
3. The column names start with capital letters, we will change them to small letters.
4. The memory usage is 13.7+ MB, we will try to study more about it and optimize it.

In [186]:
df_orders.sample(5)

Buy Ts  Revenue                   Uid
11920  2017-10-09 23:51:00     7.33   1937319664352213651
19733  2017-11-24 20:57:00     0.98    153626849896964340
22732  2017-12-08 10:14:00    11.49  10497185136870388637
35808  2018-02-19 21:40:00     3.18  10935275099267700005
50182  2018-05-31 14:57:00     7.33  14637822926831305442

### Data optimization:

Lets foud out how big the file is:

In [187]:
df_orders.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50415 entries, 0 to 50414
Data columns (total 3 columns):
Buy Ts     50415 non-null object
Revenue    50415 non-null float64
Uid        50415 non-null uint64
dtypes: float64(1), object(1), uint64(1)
memory usage: 4.4 MB


The memory usage Before is: 4.4 MB

**We will change the column names, data types, and then check the memory usage after-**

In [188]:
# Change from capital to small letters:
df_orders.columns = df_orders.columns.str.lower()
df_orders = df_orders.rename(columns = {"buy ts":"buy_ts"})
df_orders.columns

Index(['buy_ts', 'revenue', 'uid'], dtype='object')

In [189]:
#Change to Date and Time type:
df_orders['buy_ts'] =  pd.to_datetime(df_orders['buy_ts'], format='%Y-%m-%d %H:%M:%S')

**Now we'll check the memory usage after optimization:**

In [190]:
df_orders.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50415 entries, 0 to 50414
Data columns (total 3 columns):
buy_ts     50415 non-null datetime64[ns]
revenue    50415 non-null float64
uid        50415 non-null uint64
dtypes: datetime64[ns](1), float64(1), uint64(1)
memory usage: 1.2 MB


### Great, we reduced the memory usage by almost 72%!

## step 1.3 Preparation and optimization of /datasets/costs_us.csv (df_costs):<a class="anchor" id="step1.3"></a>


 [Go Up.](#T.O.C)⏫

**We will research the third file-**

In [191]:
df_costs.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2542 entries, 0 to 2541
Data columns (total 3 columns):
source_id    2542 non-null int64
dt           2542 non-null object
costs        2542 non-null float64
dtypes: float64(1), int64(1), object(1)
memory usage: 59.7+ KB


### First overlook:
1. There seems to be no "null" values, excellent!
2. There is a column that are not in the desired type: "dt" , we need to change it to Date and Time type.
3. The memory usage is 59.7+ KB, we will try to study more about it and optimize it.

In [192]:
df_costs.sample(5)

source_id          dt   costs
1005          3  2018-03-07  996.15
1537          5  2017-08-25   79.18
2516         10  2018-05-06   17.36
2149          9  2018-05-02   11.94
1269          4  2017-11-28   87.09

### Data optimization:

Lets foud out how big the file is:

In [193]:
df_costs.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2542 entries, 0 to 2541
Data columns (total 3 columns):
source_id    2542 non-null int64
dt           2542 non-null object
costs        2542 non-null float64
dtypes: float64(1), int64(1), object(1)
memory usage: 206.2 KB


The memory usage Before is: 206.2 KB

**We will change the data types, and then check the memory usage after-**

In [194]:
#Change to Date and Time type:
df_costs['dt'] =  pd.to_datetime(df_costs['dt'], format='%Y-%m-%d %H:%M:%S')

**Now we'll check the memory usage after optimization:**

In [195]:
df_costs.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2542 entries, 0 to 2541
Data columns (total 3 columns):
source_id    2542 non-null int64
dt           2542 non-null datetime64[ns]
costs        2542 non-null float64
dtypes: datetime64[ns](1), float64(1), int64(1)
memory usage: 59.7 KB


### Great, we reduced the memory usage by almost 75%!

# Step 2. Make reports and calculate metrics <a class="anchor" id="step2"></a>

 [Go Up.](#T.O.C)⏫

## step 2.1 Product:<a class="anchor" id="step2.1"></a>


 [Go Up.](#T.O.C)⏫

### How many people use it every day, week, and month?

There are three main metrics that describe the number of active users:
* DAU — the number of daily active (unique) users
* WAU — the number of weekly active users
* MAU — the number of monthly actie users <br>
**We will calculate all of them:**

To calculate the metrics we'll first create separate columns for year, month, week, and day values.

In [196]:
df_visits['visit_year']  = df_visits['start_ts'].dt.year
df_visits['visit_month'] = df_visits['start_ts'].dt.month
df_visits['visit_week']  = df_visits['start_ts'].dt.week
df_visits['visit_day']   = df_visits['start_ts'].dt.day
df_visits.sample(3)

device              end_ts  source_id            start_ts  \
52154   desktop 2017-11-15 14:45:00          4 2017-11-15 14:44:00   
300005  desktop 2018-04-15 11:43:00          4 2018-04-15 11:42:00   
281517  desktop 2017-09-06 13:21:00          2 2017-09-06 12:59:00   

                         uid  visit_year  visit_month  visit_week  visit_day  
52154   13470046523608894908        2017           11          46         15  
300005   3626928887621616656        2018            4          15         15  
281517   3768391341321534148        2017            9          36          6

**DAU-**

In [197]:
dau = df_visits.groupby(['visit_year','visit_month','visit_day']).agg({'uid':'nunique'}).reset_index(inplace=False)
#mau_mean = mau['uid'].mean()
print ("Daily Average Users: {:,}".format(int(dau.uid.mean())))


Daily Average Users: 907


In [198]:
df = pd.DataFrame({'year': dau['visit_year'],
                   'month': dau['visit_month'],
                   'day': dau['visit_day']})

dau['time'] = pd.to_datetime(df)

dau = dau.rename(columns={"uid":"users"})
fig = px.bar(dau,x='time',y='users', text='users', title='Daily Active Users (DAU) Trend')

fig.update_traces(marker_color='mediumspringgreen')

fig.update_xaxes(
    dtick="M1",
    tickformat="%b\n%Y")
fig.show()

 [Go Up.](#T.O.C)⏫

**WAU-**

In [199]:
wau = df_visits.groupby(['visit_year','visit_week']).agg({'uid':'nunique'}).reset_index(inplace=False)

print ("Weekly Average Users: {:,}".format(int(wau.uid.mean())))


Weekly Average Users: 5,716


**MAU-**

In [200]:
mau = df_visits.groupby(['visit_year','visit_month']).agg({'uid':'nunique'}).reset_index(inplace=False)

print ("Monthly Average Users: {:,}".format(int(mau.uid.mean())))


Monthly Average Users: 23,228


In [201]:
df_m = pd.DataFrame({'year': mau['visit_year'],
                   'month': mau['visit_month'],
                   'day': mau['visit_month']})
mau['time'] = pd.to_datetime(df_m)

mau = mau.rename(columns={"uid":"users"})

fig = px.bar(mau,x='time',y='users', text='users', title='Monthly Average Users (MAU) Trend')

fig.update_traces(marker_color='mediumspringgreen')


fig.update_traces(textposition='outside')


fig.update_xaxes(
    dtick="M1",
    tickformat="%b\n%Y")
fig.show()

 [Go Up.](#T.O.C)⏫

**Conclusions on DAU/WAU/MOU metrics:**<br>
* There is a very large peak of the number of active users in November, on a daily basis and a monthly basis.
* We can see that the app had a growth trend that it did not manage to maintain.  

### How many sessions are there per day? 
(One user might have more than one session.)

#### Build a df with the number of sessions pe Day-

In [202]:
#Agg and count the number of session per day-
total_sessions_daily = df_visits.groupby(
                        ['visit_year','visit_month','visit_day']).agg(
                        {'uid':'count'}).reset_index(inplace=False)

full_date = pd.DataFrame({ 'year': total_sessions_daily['visit_year'],
                          'month': total_sessions_daily['visit_month'],
                            'day': total_sessions_daily['visit_day']})

total_sessions_daily['date'] = pd.to_datetime(full_date)

total_sessions_daily = total_sessions_daily.rename(columns={"uid":"sessions"})

In [203]:
fig = px.line(total_sessions_daily, x="date", y="sessions", title='Daily Sessions')
fig.update_xaxes(
    dtick="M1",
    tickformat="%b\n%Y")
fig.update_traces(line_color='mediumspringgreen')
fig.show()

* Obviously we could have anticipated this peak in advance, since we checked on active users on a daily basis, and this is the total entries in general.<br>
It can be seen that in November the amount of entries was very large.<br>
**Is it as a result of promotion? Black Friday?**

* In April we see that there is a dramatic decrease in the number of entries up to 0 entries.<br>
**Was there a problem with the servers?**

 [Go Up.](#T.O.C)⏫

#### We now find the number of monthly sessions broken down by devices-
We will check if the is a significant difference between the devices-

In [204]:
monthly_sessions_by_device = df_visits.groupby(
                            ['visit_year','visit_month','device']).agg(
                            {'uid':'count'}).reset_index(inplace=False)


full_date = pd.DataFrame({  'year': monthly_sessions_by_device['visit_year'],
                           'month': monthly_sessions_by_device['visit_month'],
                             'day': monthly_sessions_by_device['visit_month']})

monthly_sessions_by_device['date'] = pd.to_datetime(full_date)

monthly_sessions_by_device = monthly_sessions_by_device.rename(columns={"uid":"sessions"})

monthly_sessions = monthly_sessions_by_device.groupby('date')['sessions'].sum().reset_index()

monthly_sessions_by_device['precent'] = (monthly_sessions_by_device['sessions'] /
                                         monthly_sessions_by_device.merge(monthly_sessions, on='date', how='left')['sessions_y'] * 100).round(2).astype(str) + '%'

In [205]:
fig = px.bar(monthly_sessions_by_device, x="date", y="sessions",
             text="precent", color="device",
             title="Monthly sessions Breakdown by Devices",
             color_discrete_sequence=px.colors.qualitative.Set2)

fig.update_traces(textfont_size=10)
fig.update_xaxes(dtick="M1",tickformat="%b\n%Y")
fig.show()

**A number of things can be deduced from the data:**
* The percentage of entries from the desktop remains stable throughout the period.
* Desktops device is the vast majority of entries, it can be assumed that the site's platform is more convenient.
* We need to check if there are any problems with the version of the mobile, possibly if we check we will find the reason between the difference in the sessions between 2 types of devices. 

 [Go Up.](#T.O.C)⏫

### What is the length of each session?

In [206]:
df_visits['session_duration_sec'] = (df_visits['end_ts'] - df_visits['start_ts']).dt.seconds
df_visits.sample(3)

device              end_ts  source_id            start_ts  \
201862  desktop 2018-05-03 15:04:00         10 2018-05-03 14:53:00   
242644  desktop 2017-11-30 12:33:00          4 2017-11-30 12:30:00   
261545  desktop 2018-04-25 10:28:00          4 2018-04-25 10:18:00   

                         uid  visit_year  visit_month  visit_week  visit_day  \
201862  13216107653026783144        2018            5          18          3   
242644   6395721351221665209        2017           11          48         30   
261545  17566216711450122090        2018            4          17         25   

        session_duration_sec  
201862                   660  
242644                   180  
261545                   600

In [207]:
df_visits_desk = df_visits[df_visits['device']=='desktop']
df_visits_touch = df_visits[df_visits['device']=='touch']

In [208]:
print('The average session duration length is: {:.1f}'.format(df_visits['session_duration_sec'].mean())+' seconds.')
print ("The most frquent session duration value is {} seconds and the median value is {:.0f} seconds ({} minutes)"
       .format(df_visits['session_duration_sec'].mode()[0],df_visits['session_duration_sec'].median(),df_visits['session_duration_sec'].median()/60))
print('\nThe average session duration length through Desktop is: {:.1f}'.format(df_visits_desk ['session_duration_sec'].mean())+' seconds.')
print('The average session duration length through Touch   is: {:.1f}'.format(df_visits_touch['session_duration_sec'].mean())+' seconds.')


The average session duration length is: 643.5 seconds.
The most frquent session duration value is 60 seconds and the median value is 300 seconds (5.0 minutes)

The average session duration length through Desktop is: 703.9 seconds.
The average session duration length through Touch   is: 479.6 seconds.


**Again we can see the difference between the devices.**

#### We will now see the distribution of session durations:

In [209]:
fig = px.histogram(df_visits[df_visits['session_duration_sec']<1800], x="session_duration_sec", nbins=30)
fig.update_layout(
    title_text='Session Duration Histogram', 
    xaxis_title_text='Duration (seconds)',
    yaxis_title_text='Frequancy'
)

fig.update_traces(marker_color='mediumspringgreen')
fig.show()

**We can see that:**

In [210]:
print ("Average Session Duration is {:.1f} seconds or {:.1f} minutes.".format(df_visits['session_duration_sec'].mean(),df_visits['session_duration_sec'].mean()/60))
print ("The most frquent session duration value is {} seconds and the median value is {:.0f} seconds ({} minutes)".format(df_visits['session_duration_sec'].mode()[0],df_visits['session_duration_sec'].median(),df_visits['session_duration_sec'].median()/60))

Average Session Duration is 643.5 seconds or 10.7 minutes.
The most frquent session duration value is 60 seconds and the median value is 300 seconds (5.0 minutes)


* The ditrubution looks normal and skewed to the right.
* Most sessions seem to be between 0-190 seconds (about 3 minutes).

### How often do users come back?

**First, we will perform a calculation of the stick factor-**<br>
This metric tells us how loyal the audience is — how often they return to the app

In [211]:
dau_avg = dau.users.mean()
wau_avg = wau.uid.mean()
mau_avg = mau.users.mean()

We will calculate the stickט factor for the whole period:

In [212]:
sticky_wau = int(dau_avg/wau_avg*100)
sticky_mau = int(dau_avg/mau_avg*100)
print("The sticky factor for whole period is: {}% on a weekly basis and {}% on a monthly basis.".format(sticky_wau,sticky_mau))

The sticky factor for whole period is: 15% on a weekly basis and 3% on a monthly basis.


* The sticky factor we got seems to be low.

* **We will now examine whether the sticky factor is also low in monthly base.<br>**
**We will normalize the grades so that they correspond to a monthly index from 0 to 1.**

In [213]:
mau['m_indexed_users'] = mau['users'] * 100/mau['users'].max()
dau['d_indexed_users'] = dau['users'] * 100/dau['users'].max()

In [214]:
#create stickiness over time 
d_m_au = mau.merge(dau, on=["visit_year","visit_month"])
d_m_au.head(2)

visit_year  visit_month  users_x     time_x  m_indexed_users  visit_day  \
0        2017            6    13259 2017-06-06        40.427478          1   
1        2017            6    13259 2017-06-06        40.427478          2   

   users_y     time_y  d_indexed_users  
0      605 2017-06-01        18.228382  
1      608 2017-06-02        18.318771

In [215]:
#create steaky grade per day
index_by_m = d_m_au.groupby('time_x')['d_indexed_users'].sum().reset_index(inplace=False)
index_by_m['indexed_dau_users'] = index_by_m['d_indexed_users'] * 100 / index_by_m['d_indexed_users'].max()
index_by_m.head(2)

time_x  d_indexed_users  indexed_dau_users
0 2017-06-06       461.584815          38.425845
1 2017-07-07       496.956915          41.370488

In [216]:
#Calculate steaky factor to every day equal in the same month
d_m_au = d_m_au.merge(index_by_m, on=["time_x"])
d_m_au['sticky'] = d_m_au['indexed_dau_users'] / d_m_au['m_indexed_users']
d_m_au.head(2)

visit_year  visit_month  users_x     time_x  m_indexed_users  visit_day  \
0        2017            6    13259 2017-06-06        40.427478          1   
1        2017            6    13259 2017-06-06        40.427478          2   

   users_y     time_y  d_indexed_users_x  d_indexed_users_y  \
0      605 2017-06-01          18.228382         461.584815   
1      608 2017-06-02          18.318771         461.584815   

   indexed_dau_users    sticky  
0          38.425845  0.950488  
1          38.425845  0.950488

In [217]:
#claculate the normal steaky factor to every month
d_m_au_bymonth = d_m_au.groupby('time_x')['sticky'].mean().reset_index(inplace=False)
d_m_au_bymonth['sticky'] = d_m_au_bymonth['sticky'].round(3)
d_m_au_bymonth

time_x  sticky
0  2017-06-06   0.950
1  2017-07-07   0.957
2  2017-08-08   0.950
3  2017-09-09   0.961
4  2017-10-10   0.973
5  2017-11-11   1.000
6  2017-12-12   1.003
7  2018-01-01   0.974
8  2018-02-02   0.975
9  2018-03-03   0.977
10 2018-04-04   0.960
11 2018-05-05   0.969

In [218]:
fig = px.bar(d_m_au_bymonth,x='time_x',y='sticky', text='sticky', title='Developement of Sticky Factor over months', labels=dict(time_x="Month", sticky="Normalaized Sticky Factor (DAU / MAU )"))

fig.update_traces(textposition='outside', textfont_size=13)

fig.update_traces(marker_color='mediumspringgreen')

fig.update_xaxes(
    dtick="M1",
    tickformat="%b\n%Y")
fig.update_yaxes(
    range=[0.93,1.01])

fig.show()

**The following conclusions can be drawn from the data:**

* First at the end of the given period it seems that the steaky factor increases.
* There seems to be a peak in the months of November and December, which is very worth checking, whether it is as a result of actions taken in the company, or only out of **seasonality**.
* After a good rise, there has been a significant decline whose peak is in April.

### If we want to attract investors to the company, we should very much understand  the data in November and December and conduct research on this period.

 [Go Up.](#T.O.C)⏫

**We will now clarify the retention factor-**
- We will divide the users into cohorts according to the time of their first visit, so that we can examine in depth each and every group

calculate first visit date:

In [219]:
#First we need to know the first time that the user visited
first_visit_date = df_visits.groupby('uid')['start_ts'].min()
first_visit_date.name = 'first_visits_datetime'
visits_cohort = df_visits.join(first_visit_date,on='uid')
visits_cohort.head(2)

device              end_ts  source_id            start_ts  \
0    touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00   
1  desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00   

                    uid  visit_year  visit_month  visit_week  visit_day  \
0  16879256277535980062        2017           12          51         20   
1    104060357244891740        2018            2           8         19   

   session_duration_sec first_visits_datetime  
0                  1080   2017-12-20 17:20:00  
1                  1680   2018-02-19 16:53:00

Adding the curent visit month and the first visit month:


In [220]:
#Adding the curent visit month and the first visit month
visits_cohort['visits_month'] = visits_cohort['start_ts'].astype('datetime64[M]')
visits_cohort['first_visits_month'] = visits_cohort['first_visits_datetime'].astype('datetime64[M]')
visits_cohort.head(2)

device              end_ts  source_id            start_ts  \
0    touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00   
1  desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00   

                    uid  visit_year  visit_month  visit_week  visit_day  \
0  16879256277535980062        2017           12          51         20   
1    104060357244891740        2018            2           8         19   

   session_duration_sec first_visits_datetime visits_month first_visits_month  
0                  1080   2017-12-20 17:20:00   2017-12-01         2017-12-01  
1                  1680   2018-02-19 16:53:00   2018-02-01         2018-02-01

In [221]:
#calculate user lifetime within the cohort for each row of the DataFrame
visits_cohort['cohort_lifetime'] = visits_cohort['visits_month'] - visits_cohort['first_visits_month']
visits_cohort['cohort_lifetime'] = visits_cohort['cohort_lifetime']/np.timedelta64(1,'M')
visits_cohort['cohort_lifetime'] = visits_cohort['cohort_lifetime'].round().astype('int')
visits_cohort.head(2)

device              end_ts  source_id            start_ts  \
0    touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00   
1  desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00   

                    uid  visit_year  visit_month  visit_week  visit_day  \
0  16879256277535980062        2017           12          51         20   
1    104060357244891740        2018            2           8         19   

   session_duration_sec first_visits_datetime visits_month first_visits_month  \
0                  1080   2017-12-20 17:20:00   2017-12-01         2017-12-01   
1                  1680   2018-02-19 16:53:00   2018-02-01         2018-02-01   

   cohort_lifetime  
0                0  
1                0

Group the data by cohort and lifetime and find the number of active users at a certain lifetime month for each cohort:


In [222]:
#group the data by cohort and lifetime and find the number of active users at a certain lifetime month for each cohort
cohorts = visits_cohort.groupby(['first_visits_month','cohort_lifetime']).agg({'uid':'count'}).reset_index()
cohorts.head(5)

first_visits_month  cohort_lifetime    uid
0         2017-06-01                0  16505
1         2017-06-01                1   2412
2         2017-06-01                2   1758
3         2017-06-01                3   2260
4         2017-06-01                4   2679

Add the initial users in every cohort  :

In [223]:
#find initial users counts at week 0  
initial_users_count = cohorts[cohorts['cohort_lifetime'] == 0][['first_visits_month','uid']]
initial_users_count = initial_users_count.rename(columns={'uid':'cohort_users'}) 
cohorts = cohorts.merge(initial_users_count,on='first_visits_month')

cohorts.head(5)

first_visits_month  cohort_lifetime    uid  cohort_users
0         2017-06-01                0  16505         16505
1         2017-06-01                1   2412         16505
2         2017-06-01                2   1758         16505
3         2017-06-01                3   2260         16505
4         2017-06-01                4   2679         16505

**Now we can calculate the retantion rate for every period of time by cohort- (remain_users_period[N]/initial_users) :**

In [224]:
#calculate retention
cohorts['retention'] = cohorts['uid']/cohorts['cohort_users']

cohorts.head(5)

first_visits_month  cohort_lifetime    uid  cohort_users  retention
0         2017-06-01                0  16505         16505   1.000000
1         2017-06-01                1   2412         16505   0.146138
2         2017-06-01                2   1758         16505   0.106513
3         2017-06-01                3   2260         16505   0.136928
4         2017-06-01                4   2679         16505   0.162314

Prepare pivot for heatmap:


In [225]:
retention_pivot = cohorts.pivot_table(index='first_visits_month',columns='cohort_lifetime',values='retention',aggfunc='sum')
retention_pivot

cohort_lifetime      0         1         2         3         4         5   \
first_visits_month                                                          
2017-06-01          1.0  0.146138  0.106513  0.136928  0.162314  0.180067   
2017-07-01          1.0  0.074987  0.075765  0.083031  0.090490  0.069992   
2017-08-01          1.0  0.104973  0.089590  0.091426  0.078577  0.065991   
2017-09-01          1.0  0.113601  0.100166  0.072725  0.050680  0.049331   
2017-10-01          1.0  0.107683  0.068860  0.048196  0.041654  0.038953   
2017-11-01          1.0  0.114089  0.066665  0.056219  0.042682  0.025903   
2017-12-01          1.0  0.075871  0.049713  0.038936  0.022521  0.022688   
2018-01-01          1.0  0.087295  0.055485  0.029047  0.024941       NaN   
2018-02-01          1.0  0.077559  0.030587  0.027115       NaN       NaN   
2018-03-01          1.0  0.055664  0.037193       NaN       NaN       NaN   
2018-04-01          1.0  0.074958       NaN       NaN       NaN       NaN   
2018-05-01          1.0       NaN       NaN       NaN       NaN       NaN   

cohort_lifetime           6         7         8         9         10        11  
first_visits_month                                                              
2017-06-01          0.164435  0.135232  0.127779  0.120024  0.098334  0.098031  
2017-07-01          0.060846  0.062208  0.052737  0.038661  0.036975       NaN  
2017-08-01          0.053579  0.063543  0.044139  0.040119       NaN       NaN  
2017-09-01          0.046737  0.030242  0.030190       NaN       NaN       NaN  
2017-10-01          0.025416  0.025676       NaN       NaN       NaN       NaN  
2017-11-01          0.026624       NaN       NaN       NaN       NaN       NaN  
2017-12-01               NaN       NaN       NaN       NaN       NaN       NaN  
2018-01-01               NaN       NaN       NaN       NaN       NaN       NaN  
2018-02-01               NaN       NaN       NaN       NaN       NaN       NaN  
2018-03-01               NaN       NaN       NaN       NaN       NaN       NaN  
2018-04-01               NaN       NaN       NaN       NaN       NaN       NaN  
2018-05-01               NaN       NaN       NaN       NaN       NaN       NaN

Assighninig function to handle withe the plotly lab:

In [226]:
def df_to_plotly_pcnt(df):
    return {'z': (df.values*100).round(1).tolist(),
            'x': df.columns.tolist(),
            'y': df.index.tolist()}
def df_to_plotly(df):
    return {'z': (df.values).round(2).tolist(),
            'x': df.columns.tolist(),
            'y': df.index.tolist()}

#### Retention Heatmap:

In [227]:
fig = go.Figure(data=go.Heatmap(df_to_plotly_pcnt(retention_pivot),colorscale='tealgrn'))

fig.update_yaxes(autorange="reversed")

fig.update_layout(
    title='User Retention (%)',
    xaxis_nticks=12,
    yaxis_nticks=12
)
fig.update_layout(
    autosize=False,
    width=800,
    height=800)

fig['layout']['xaxis']['type'] = 'category'
fig['layout']['yaxis']['type'] = 'date'
fig.update_xaxes(tickfont=dict(family='Rockwell', color='forestgreen', size=14))
fig.update_yaxes(tickfont=dict(family='Rockwell', color='forestgreen', size=14))


fig.show()

**From the retention heatmap we can see:**

* The cohort with the highest retention rate is the first group (June 2017).<br> Did they receive benefits that others do not have? <br>Have we put more effort into retention?
* In the group of March 2018 it seems that there are very low retention rate, did we tried to do something different in those months?<br> It should be check that so that they do not repeat incorrect actions.
* It is necessary to check how much we paid so that the retention effort will be high in the months with the highest retention rate.

 [Go Up.](#T.O.C)⏫

## step 2.2 Sales: <a class="anchor" id="step2.2"></a>


 [Go Up.](#T.O.C)⏫

### When do people start buying? 

**We will look at the average time it takes a customer to make a purchase from the moment they first visit the site.**<br>
We will first check this according to the source from which the customer came:

In [228]:
#Fimnd the first visit date
first_order_date = df_orders.groupby(['uid'])['buy_ts'].min().reset_index(inplace=False)
first_order_date.name = 'first_visits_datetime'
first_order_date = first_order_date.join(first_visit_date, on='uid')
first_order_date.head(2)

uid              buy_ts first_visits_datetime
0   313578113262317 2018-01-03 21:51:00   2017-09-18 22:49:00
1  1575281904278712 2017-06-03 10:13:00   2017-06-03 10:13:00

In [229]:
#Checking how much days from first visit to first order
first_order_date['conversion_lag'] = first_order_date['buy_ts'] - first_order_date['first_visits_datetime']
first_order_date['conversion_lag'] = first_order_date['conversion_lag']/np.timedelta64(1,'D')
first_order_date.head(2)

uid              buy_ts first_visits_datetime  conversion_lag
0   313578113262317 2018-01-03 21:51:00   2017-09-18 22:49:00      106.959722
1  1575281904278712 2017-06-03 10:13:00   2017-06-03 10:13:00        0.000000

In [230]:
#Find the avg conversion lag per source
source_per_user = df_visits.groupby('uid')['source_id'].min()
first_order_date = first_order_date.join(source_per_user, on='uid')
conversion_lag_per_source = first_order_date.groupby('source_id')['conversion_lag'].mean().reset_index(inplace=False)
conversion_lag_per_source.head(2)

source_id  conversion_lag
0          1       23.881913
1          2       24.692723

In [231]:
#Find the first order date per uid
first_order_date = df_orders.groupby(['uid'])['buy_ts'].min().reset_index(inplace=False)
first_order_date.name = 'first_visits_datetime'
first_order_date = first_order_date.join(first_visit_date, on='uid')
first_order_date.sample(2)

uid              buy_ts first_visits_datetime
34103  17228501771982252216 2018-04-26 16:21:00   2018-04-26 16:11:00
28034  14169561490594089902 2018-04-06 16:59:00   2018-01-12 13:19:00

In [232]:
#Find the days between the first visit to first order
first_order_date['conversion_lag'] = first_order_date['buy_ts'] - first_order_date['first_visits_datetime']
first_order_date['conversion_lag'] = first_order_date['conversion_lag']/np.timedelta64(1,'D')
first_order_date['conversion_lag'] = first_order_date['conversion_lag'].round().astype('int')
first_order_date.sample(2)

uid              buy_ts first_visits_datetime  \
9782    4946312528225528842 2017-11-16 11:45:00   2017-11-16 09:59:00   
24020  12147111747510205477 2017-11-08 00:32:00   2017-11-08 00:31:00   

       conversion_lag  
9782                0  
24020               0

In [233]:
#Add the source id to the uid
source_per_user = df_visits.groupby('uid')['source_id'].min()
first_order_date = first_order_date.join(source_per_user, on='uid')
first_order_date.sample(2)

uid              buy_ts first_visits_datetime  \
21204  10720407376170510995 2017-11-17 13:55:00   2017-11-07 12:09:00   
26606  13444960617174387228 2017-11-09 11:47:00   2017-11-09 11:44:00   

       conversion_lag  source_id  
21204              10          3  
26606               0          4

In [234]:
#Conversion_lag_per_source
conversion_lag_per_source = first_order_date.groupby('source_id')['conversion_lag'].mean().reset_index(inplace=False)
conversion_lag_per_source['conversion_lag'] = conversion_lag_per_source['conversion_lag'].round(2)
conversion_lag_per_source

source_id  conversion_lag
0          1           23.87
1          2           24.69
2          3           16.31
3          4           12.51
4          5            7.15
5          7            0.00
6          9           30.84
7         10            5.74

In [235]:
fig = px.bar(conversion_lag_per_source, x="source_id", y="conversion_lag", 
             text="conversion_lag", 
             title="Avg. Conversion Lag (days) per source", 
             labels=dict(source_id="Source ID", conversion_lag="Days"))

fig.update_traces(textfont_size=15, marker_color = 'firebrick')
fig.update_layout(xaxis = dict(
    tickmode = 'linear',
    tick0 = 1,
    dtick = 1
))
fig.update_xaxes(showticklabels=True, ticks="inside")
fig.show()

**From the data it can be concluded that:**

* Source number 10 is the source with the shortest conversion lag, source number 5 poset a place after it.<br>
**Is the funnel that taken by the users of these sources is the same funnel that the other sources go?**<br>
We should check this out and learn from one source to another.<br><br>
* The source with the highest conversion lag is source number 9.<br>
It is possible and worthwhile to check why it is ineffective compared to others, maybe the target audience coming from this source may need a different treatment.

 [Go Up.](#T.O.C)⏫

**We will now display the conversion time frequency in the bar chart:**

In [236]:
conversion_lag_range = first_order_date.groupby('conversion_lag')['uid'].count().reset_index(inplace=False)
conversion_lag_range.head(2)

conversion_lag    uid
0               0  25217
1               1   1779

In [237]:
fig = px.bar(conversion_lag_range[(conversion_lag_range['conversion_lag'] < 31) & (conversion_lag_range['conversion_lag'] > 0.5)],
             y="conversion_lag",x="uid", title='Conversion Lag',
             labels=dict(uid="Amount of conversions",
                         conversion_lag="Days to Conversion"),orientation='h')
fig.update_yaxes(autorange="reversed")
fig.update_layout(
    
    yaxis_nticks=31
)

fig.update_traces(textfont_size=15, marker_color = 'firebrick')
fig.show()

- Good news!, there seems to be a very large group of users making the first purchase in the first three days.
* On the other hand - there is a **"long tail"** of users which takes them over 3 days to make a first purchase.

It seems that the more time passes between the first visit, the less likely the customer is to make a purchase.<br>
It is worthwhile to make an effort to be able to convert users on the first day of visiting the site, the number of conversion rates should be reduced in the days away from the 0 day!


 [Go Up.](#T.O.C)⏫

### How many orders do they make during a given period of time?

**We will now check the average amount of orders on a monthly basis in this way-**<br>
We will divide the users into groups defined for the first month they visited the site, and then we will check the average purchases per group:

In [238]:
#Create order tble with cohorts
amount_of_orders = df_orders.merge(visits_cohort, on='uid')
amount_of_orders.head(2)

buy_ts  revenue                   uid   device  \
0 2017-06-01 00:10:00    17.00  10329302124590727494  desktop   
1 2017-06-01 00:25:00     0.55  11627257723692907447  desktop   

               end_ts  source_id            start_ts  visit_year  visit_month  \
0 2017-06-01 00:11:00          1 2017-06-01 00:09:00        2017            6   
1 2017-06-01 00:25:00          2 2017-06-01 00:14:00        2017            6   

   visit_week  visit_day  session_duration_sec first_visits_datetime  \
0          22          1                   120   2017-06-01 00:09:00   
1          22          1                   660   2017-06-01 00:14:00   

  visits_month first_visits_month  cohort_lifetime  
0   2017-06-01         2017-06-01                0  
1   2017-06-01         2017-06-01                0

In [239]:
#Total purchses in terms of cohorts
orders_per_month = amount_of_orders.groupby('first_visits_month')['buy_ts'].count().reset_index(inplace=False)
orders_per_month

first_visits_month  buy_ts
0          2017-06-01  447902
1          2017-07-01   23980
2          2017-08-01   50975
3          2017-09-01   32216
4          2017-10-01   26217
5          2017-11-01   58848
6          2017-12-01   29232
7          2018-01-01   24235
8          2018-02-01   19230
9          2018-03-01   34662
10         2018-04-01   10594
11         2018-05-01    3716

In [240]:
#Number of unique uid in every cohort
unique_users_per_month = amount_of_orders.groupby('first_visits_month')['uid'].nunique().reset_index(inplace=False)
unique_users_per_month

first_visits_month   uid
0          2017-06-01  2923
1          2017-07-01  2458
2          2017-08-01  1721
3          2017-09-01  3058
4          2017-10-01  4678
5          2017-11-01  4262
6          2017-12-01  4074
7          2018-01-01  3119
8          2018-02-01  3186
9          2018-03-01  2838
10         2018-04-01  1890
11         2018-05-01  2316

In [241]:
#Put the DF together in order to calculate the avg transaction in terms of cohrts for all period
orders_per_month = pd.merge(orders_per_month,unique_users_per_month)

In [242]:
#Calculate the transaction per user in terms of cohorts
orders_per_month['transactions_per_user'] = (orders_per_month['buy_ts'] / orders_per_month['uid']).round(2)
orders_per_month

first_visits_month  buy_ts   uid  transactions_per_user
0          2017-06-01  447902  2923                 153.23
1          2017-07-01   23980  2458                   9.76
2          2017-08-01   50975  1721                  29.62
3          2017-09-01   32216  3058                  10.53
4          2017-10-01   26217  4678                   5.60
5          2017-11-01   58848  4262                  13.81
6          2017-12-01   29232  4074                   7.18
7          2018-01-01   24235  3119                   7.77
8          2018-02-01   19230  3186                   6.04
9          2018-03-01   34662  2838                  12.21
10         2018-04-01   10594  1890                   5.61
11         2018-05-01    3716  2316                   1.60

In [243]:
fig = px.bar(orders_per_month, x="first_visits_month", 
             y="transactions_per_user", text="transactions_per_user", 
             title="Avg. Transactions per User by First Visit Month", 
             labels=dict(first_visits_month="Cohort Month",
                         transactions_per_user="Avg. Transactions per User"))

fig.update_traces(textfont_size=11, marker_color = 'firebrick')
fig.update_xaxes(
    dtick="M1",
    tickformat="%b\n%Y")
fig.show()

**From the graph it can be seen that:**

* The group of users who first visited in June 2017 dramatically leads the rest of the groups in the average number of purchases per user with 153 purchases per user for all the period.<br>
Do that users is "Favorites"? We have to put effort into this figure if you want to replicate the success.

 [Go Up.](#T.O.C)⏫

### What is the average purchase size?

**We will calculate the average purchase value for each user in his cohort.(cohorts as we define above).**<br> The calculation will be made as follows: the amount of revenue divided by the number of purchases.


In [244]:
#Create  a pivot table in order to calculate the revenue and times of purcheses in terms of cohorts
value_per_month = amount_of_orders.pivot_table(index='first_visits_month', values='revenue',aggfunc=['sum','count']).reset_index(inplace=False)
value_per_month.columns = ['first_visits_month', 'sum_revenue', 'amount_of_transactions']
value_per_month


first_visits_month   sum_revenue  amount_of_transactions
0          2017-06-01  3.929833e+06                  447902
1          2017-07-01  1.686924e+05                   23980
2          2017-08-01  5.441894e+05                   50975
3          2017-09-01  1.229545e+06                   32216
4          2017-10-01  1.710361e+05                   26217
5          2017-11-01  2.471403e+05                   58848
6          2017-12-01  2.175067e+05                   29232
7          2018-01-01  1.341091e+05                   24235
8          2018-02-01  8.197011e+04                   19230
9          2018-03-01  1.452694e+05                   34662
10         2018-04-01  7.686662e+04                   10594
11         2018-05-01  1.604881e+04                    3716

In [245]:
#Calculate the avg revenue per user in every cohort
value_per_month['avg_conv_value'] = (value_per_month['sum_revenue'] / value_per_month['amount_of_transactions']).round(2)
value_per_month

first_visits_month   sum_revenue  amount_of_transactions  avg_conv_value
0          2017-06-01  3.929833e+06                  447902            8.77
1          2017-07-01  1.686924e+05                   23980            7.03
2          2017-08-01  5.441894e+05                   50975           10.68
3          2017-09-01  1.229545e+06                   32216           38.17
4          2017-10-01  1.710361e+05                   26217            6.52
5          2017-11-01  2.471403e+05                   58848            4.20
6          2017-12-01  2.175067e+05                   29232            7.44
7          2018-01-01  1.341091e+05                   24235            5.53
8          2018-02-01  8.197011e+04                   19230            4.26
9          2018-03-01  1.452694e+05                   34662            4.19
10         2018-04-01  7.686662e+04                   10594            7.26
11         2018-05-01  1.604881e+04                    3716            4.32

In [246]:
fig = px.bar(value_per_month, x="first_visits_month", 
                              y="avg_conv_value", text="avg_conv_value", 
                              title="Avg. Purchase Value per Transaction by First Visit Month", 
                              labels=dict(first_visits_month="Cohort Month", 
                                          avg_conv_value="Avg. Value per Transaction"))

fig.update_traces(textfont_size=14.5, marker_color = 'firebrick')
fig.update_xaxes(
    dtick="M1",
    tickformat="%b\n%Y")
fig.show()

**From the graph it can be seen that:**

* The cohort of September 2017 has the highest average purchase value! Have we put a lot of effort into getting those customers?<br>
If not, how can you learn from it?<br>
* We can check the average amount of purchases and multiply by the average value per purchase to get the average revenue value from each cohort, or alternatively, check the LTV rate.

### How much money do they bring? (LTV)

LTV (lifetime value) is the customer's lifetime value. It's the total amount of money a customer brings to the company on average by making purchases.<br>
When calculating LTV, we will consider the gross profit from a customer per period.

In [247]:
#Adding order monthe to orders table
df_orders['order_month'] = df_orders['buy_ts'].astype('datetime64[M]')
df_orders.head(2)

buy_ts  revenue                   uid order_month
0 2017-06-01 00:10:00    17.00  10329302124590727494  2017-06-01
1 2017-06-01 00:25:00     0.55  11627257723692907447  2017-06-01

Find the first order to every uid -


In [248]:
#find the first order to evere uid 
first_orders = df_orders.groupby('uid').agg({'order_month': 'min'}).reset_index()
first_orders.columns = ['uid', 'first_order_month']
first_orders.head(2)

uid first_order_month
0   313578113262317        2018-01-01
1  1575281904278712        2017-06-01

Find the initial users that start in every cohort-

In [249]:
#find the initial users that start in every cohort
cohort_sizes = first_orders.groupby('first_order_month').agg({'uid': 'nunique'}).reset_index()
cohort_sizes.columns = ['first_order_month', 'n_buyers']
cohort_sizes

first_order_month  n_buyers
0         2017-06-01      2023
1         2017-07-01      1923
2         2017-08-01      1370
3         2017-09-01      2581
4         2017-10-01      4340
5         2017-11-01      4081
6         2017-12-01      4383
7         2018-01-01      3373
8         2018-02-01      3651
9         2018-03-01      3533
10        2018-04-01      2276
11        2018-05-01      2988
12        2018-06-01         1

In [250]:
#Add first order month to orders table
df_orders_1 = pd.merge(df_orders,first_orders, on='uid')
#aggregate the revenue per month and categorize by cohort time
cohorts = df_orders_1.groupby(['first_order_month','order_month']).agg({'revenue': 'sum'}).reset_index()
#Add the cohort initial size
df_ltv = pd.merge(cohort_sizes, cohorts, on='first_order_month')
df_ltv.head(2)

first_order_month  n_buyers order_month  revenue
0        2017-06-01      2023  2017-06-01  9557.49
1        2017-06-01      2023  2017-07-01   981.82

In [251]:
#Add calculation of raw reveneu (gross profit) , life time  and LTV per month in terms of cohorts
df_ltv['gp'] = df_ltv['revenue'] 
df_ltv['lt'] = (df_ltv['order_month'] - df_ltv['first_order_month']) / np.timedelta64(1, 'M')
df_ltv['lt'] = df_ltv['lt'].round().astype('int')
df_ltv['ltv'] = df_ltv['gp'] / df_ltv['n_buyers']
df_ltv.head(2)


first_order_month  n_buyers order_month  revenue       gp  lt       ltv
0        2017-06-01      2023  2017-06-01  9557.49  9557.49   0  4.724414
1        2017-06-01      2023  2017-07-01   981.82   981.82   1  0.485329

In [252]:
ltv_map = df_ltv.pivot_table(index='first_order_month', columns='lt', values='ltv', aggfunc='mean').round(2)


In [253]:
fig = go.Figure(data=go.Heatmap(df_to_plotly(ltv_map),colorscale='rdbu'))

fig.update_yaxes(autorange="reversed")

fig.update_layout(
    title='Monthly LTV by User Cohort ($)',
    xaxis_nticks=12,
    yaxis_nticks=13
)
fig.update_layout(
    autosize=False,
    width=800,
    height=800)

fig['layout']['xaxis']['type'] = 'category'
fig['layout']['yaxis']['type'] = 'date'
fig.update_xaxes(tickfont=dict(family='Rockwell', color='crimson', size=14))
fig.update_yaxes(tickfont=dict(family='Rockwell', color='crimson', size=14))


fig.show()

**From the LTV heatmap we can see:**

* The group with the highest LTV rating over time is the September 2017 group, which makes sense and is consistent with the conclusion we found earlier regarding the average purchase per user.<br>
It is worthwhile to see if the users from this group came from a specific source.

In [254]:
revenue_by_user = df_orders.groupby(['uid'])['revenue'].sum().reset_index(inplace=False)
revenue_by_user = revenue_by_user.join(source_per_user, on='uid')
revenue_by_user.head(2)

uid  revenue  source_id
0   313578113262317     0.55          2
1  1575281904278712     3.05         10

**Now we want to check which source is the most lucrative LTV source to get a wider picture-**

In [255]:
#add source id
revenue_by_source = revenue_by_user.pivot_table(index='source_id', values=['revenue'], aggfunc=['mean']).reset_index(inplace=False)
revenue_by_source.columns = ['source_id', 'avg_ltv']
revenue_by_source['avg_ltv'] = revenue_by_source['avg_ltv'].round(2)

In [256]:
fig = px.bar(revenue_by_source, x="source_id", 
             y="avg_ltv", 
             text="avg_ltv", 
             title="Avg. User Life Time Value (LTV) per source", 
             labels=dict(source_id="Source ID", avg_ltv="Avg. Life Time Value"))

fig.update_traces(textfont_size=14.5, marker_color = 'firebrick')
fig.update_xaxes(showticklabels=True, ticks="inside")
fig.update_layout(xaxis = dict(
        tickmode = 'linear',
        tick0 = 1,
        dtick = 1
    ))
fig.show()

**The differences are certainly noticeable-**

* Source 1 brings the most profitable users.
* Sources 7 and 10 are at the bottom, they bring in unprofitable users (on the other hand source 10 has a very low conversion time it may be worthwhile to make an effort in making it attract more profitable users).
* It is necessary to check more data, since the LTV may be low but the amount of users coming from these sources is very high.

## step 2.3 Marketing: <a class="anchor" id="step2.3"></a>


 [Go Up.](#T.O.C)⏫

### How much money was spent? 
(per source)

To complete the analysis, we will now look at how much is it cost to acquisition the users, we will check the costs per source.

**We will sum up all the costs by source-**

In [257]:
cost_per_source = df_costs.groupby('source_id')['costs'].sum().reset_index(inplace=False)
cost_per_source['costs_1'] =cost_per_source['costs']
cost_per_source['costs_1'] = cost_per_source.apply(lambda x: "{:,}".format(x['costs_1'].astype('int')), axis=1)
#cost_per_source['costs_1'] = 
cost_per_source

source_id      costs  costs_1
0          1   20833.27   20,833
1          2   42806.04   42,806
2          3  141321.63  141,321
3          4   61073.60   61,073
4          5   51757.10   51,757
5          9    5517.49    5,517
6         10    5822.49    5,822

In [258]:
fig = px.bar(cost_per_source, x="source_id",
             y="costs_1", text="costs_1", 
             title="Total Investment by source", 
             labels=dict(source_id="Source ID",
                        costs="Total Investment (USD)"),
            )

fig.update_traces( textfont_size=14,marker_color ='steelblue')
fig.update_xaxes(showticklabels=True, ticks="inside")

fig.update_layout(xaxis = dict(
        tickmode = 'linear',
        tick0 = 1,
        dtick = 1
    ))
fig.show()

**We can see from the cost graph per source-**

* There is a lot of investment in source number 3. This investment does not match the LTV rate we examined earlier, there is a high investment and a low return.<br> Need to check if it is worth continuing to invest in this source.
* Source 1 seems to be a "winning" source! Not a big investment compared to most sources, and on the other hand a very high return on the LTV rate!
* Source 10 again catches our attention, there is a very low investment, we checked first and found that the conversion time is very short, need to think about how to optimize it so that its LTV rate will increase.

### How much did customer acquisition from each of the sources cost? (CAC)


CAC (customer acquisition cost) is the cost of attracting a customer—the money a new customer costs a company. The clculation is - total_costs/unique_users.

In [259]:
revenue_by_user = df_orders.groupby(['uid'])['revenue'].sum().reset_index(inplace=False)
revenue_by_user = revenue_by_user.join(source_per_user, on='uid')
revenue_by_user.head(2)

uid  revenue  source_id
0   313578113262317     0.55          2
1  1575281904278712     3.05         10

In [260]:
users_per_source = revenue_by_user.groupby('source_id')['uid'].nunique().reset_index(inplace=False)
users_per_source

source_id   uid
0          1  7138
1          2  5336
2          3  9619
3          4  8138
4          5  4879
5          7     1
6          9   527
7         10   885

In [261]:
users_per_source.columns = ['source_id', 'unique_users']
cost_per_source = cost_per_source.merge(users_per_source, on='source_id')
cost_per_source['CAC'] = (cost_per_source['costs'] / cost_per_source['unique_users']).round(2)


In [262]:
fig = px.bar(cost_per_source, x="source_id", y="CAC", text="CAC", 
             title="Avg. User Acquisition Cost by source", 
             labels=dict(source_id="Source ID", CAC="Avg. CAC"))

fig.update_traces(textfont_size=14,marker_color ='steelblue')
fig.update_xaxes(showticklabels=True, ticks="inside")
fig.update_layout(xaxis = dict(
        tickmode = 'linear',
        tick0 = 1,
        dtick = 1
        ))
fig.show()

**Now that we have this data, we can perform the calculation that will tell us whether our investment has returned itself from source and source (ROI)**

### How worthwhile where the investments? (ROI)

In [263]:
source_income = revenue_by_user.pivot_table(index='source_id', values=['revenue'], aggfunc=['sum']).reset_index(inplace=False)

source_income.columns = ['source_id', 'rev']

cost_per_source = cost_per_source.merge(source_income, on='source_id')

cost_per_source['roi'] = (cost_per_source['rev'] / cost_per_source['costs'])

cost_per_source['roi'] = cost_per_source['roi'].map('%{:,.2f}'.format)

In [264]:
fig = px.bar(cost_per_source, x="source_id", y="roi", 
             text="roi", 
             title="Return on Investment(ROI) by source", 
             labels=dict(source_id="Source ID", 
                         roi="Return on Investment(ROI)"))


fig.update_traces(textfont_size=15,marker_color ='steelblue')
fig.update_xaxes(showticklabels=True, ticks="inside")
fig.update_layout(xaxis = dict(
        tickmode = 'linear',
        tick0 = 1,
        dtick = 1
    ))
fig.show()

**The most important graph so far in business terms-**

* It can be clearly seen that source number 1 is the source with the most profitability.
* Source number 2 covers its costs and quite a bit more, is this a positive trend? We'll need to explore more.
* Regarding the other sources, it seems that decisions are required to be made or alternatively the sources with the chances of being profitable are chosen.

# Step 3. Conclusion
I'll advise marketing experts how much money to invest and where. <a class="anchor" id="step3"></a>

 [Go Up.](#T.O.C)⏫

## Conclusions and Recommendations Report:

### I'll start with the facts:
**Sources-**
1. Source 1 is the most profitable and worthwhile source currently available.<br>From that source come the most profitable users to the company.
2. Source 2 is a source that has the potential to bring in profitable customers.
3. Sources 3 and 9 are non-profit sources.
4. Sources 10 and 5 are the sources with the lowest conversion time (5-7 days).
5. Source 3 is the source with the largest financial investment (141K).

**User Cohorts-**
1. Users cohort "June 2017" is the cohort with the most transactions per user.
2. Also, the "June 2017" cohort has the highest retention rating over time.
3. The "March 2018" cohort has the lowest retention rating over time.
4. The "September 2017" cohort has the highest LTV rating over time.

**Devices-**
1. About 70% of the sessions are performed through the desktop and the rest through mobile devices.
2. The average time for a session through the desktop is about 704 seconds (11 minutes).
3. The average time for a session via mobile devices is about 480 seconds (8 minutes).

### Recommendations:
**If the company is interested in expanding the user audience-**
1. I would recommend investing more to divert a budget from source number 3 (the least profitable) to source number 1 to bring in more profitable users.
2. I would recommend shifting a budget from source number 3 to source number 2 to bring it to significant growth.
3. Perform analysis and research on the "June 2017" cohort to see how the high conservation ratio is maintained in this cohort, and apply it in other cohorts, and in new cohorts.


**Regarding the use of budget sources-**
1. My recommendation is to stop investing in sources 5 and 3 (or divert the budget to other sources as I mentioned).
2. If the company is recruiting investors, additional funds can be invested to strengthen the stickiness factor, so that investors will see that although the company is not yet profitable enough, its users return and use the service frequently, which shows very high potential for future success and profitability.

**Another recommendation is to test the funnels at each and every source, and especially at the mobile devices.**

 [Go Up.](#T.O.C)⏫